In [1]:
# !pip show openai-whisper

In [2]:
%cd ..
!ls
import os
from dataclasses import dataclass, field, replace
from typing import TYPE_CHECKING, Dict, Iterable, List, Optional, Sequence, Tuple, Union
import whisper_openAI.whisper as whisper
import torch
from whisper_openAI.whisper.tokenizer import Tokenizer, get_tokenizer
import torch
import torch.nn.functional as F
from torch import Tensor

# We get the acoustic embeddings from Whisper Large V2
# model,processor = whisper.load_model("large-v2")
model,processor = whisper.load_model("medium")

/home/data2/jindaznb/jslpnb/mllm/Whispering-LLaMA
convert_hf_checkpoint.py	   environment.yml  Inference  requirements.txt
data_preparation		   generate	    LICENSE    training
demo.ipynb			   gitignore.sh     lit_llama  weights
EMNLP__4032_Whispering_LLaMA_.pdf  images	    README.md  whisper_openAI


In [3]:
model.eval()

Whisper(
  (encoder): AudioEncoder(
    (conv1): Conv1d(80, 1024, kernel_size=(3,), stride=(1,), padding=(1,))
    (conv2): Conv1d(1024, 1024, kernel_size=(3,), stride=(2,), padding=(1,))
    (blocks): ModuleList(
      (0-23): 24 x ResidualAttentionBlock(
        (attn): MultiHeadAttention(
          (query): Linear(in_features=1024, out_features=1024, bias=True)
          (key): Linear(in_features=1024, out_features=1024, bias=False)
          (value): Linear(in_features=1024, out_features=1024, bias=True)
          (out): Linear(in_features=1024, out_features=1024, bias=True)
        )
        (attn_ln): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (mlp): Sequential(
          (0): Linear(in_features=1024, out_features=4096, bias=True)
          (1): GELU(approximate='none')
          (2): Linear(in_features=4096, out_features=1024, bias=True)
        )
        (mlp_ln): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
      )
    )
    (ln_post): LayerNorm((

In [4]:
pwd

'/home/data2/jindaznb/jslpnb/mllm/Whispering-LLaMA'

In [5]:
import json
# The below is the json file you can generate using the "To generatn-best hyporhesis.ipynb" notebook; Need to further tokenize the hypothesis

with open(f'Inference/gs_inferences/17Science and Technology.json', "r") as file: #change
    test_data = json.load(file)

In [6]:
test_data

[{'POD0000006044_S0000046': {'temp': 0.9299999999999999,
   'path': '/home/data2/cache/downloads/extracted/7f1da8ec06736a8c2a9b36855e77a8f78791bbad1cec6dc82d38dd63eb6bb0c7/s_chunks_0000/POD0000006044_S0000046.wav',
   'ground_truth': "it's in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data.",
   'inference': ['and in a way its very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'and in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'and in some ways very similar to some of the challenges that companies are dealing with today in terms ofs streaming data',
    'and its in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'and similarly to some of the challenges that companies are dealing with today in terms of streaming data'

In [7]:
# !pip install safetensors

In [8]:
"""Implementation derived from https://github.com/tloen/alpaca-lora"""
import sys
from pathlib import Path
import torch
import requests
import json
import os 

from lit_llama.tokenizer import Tokenizer
from tqdm import tqdm

/home/jinda/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/jinda/.local/lib/python3.10/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
/home/jinda/anaconda3/envs/WhisperingLLaMA/lib/python3.10/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: '/home/jinda/anaconda3/envs/WhisperingLLaMA/lib/python3.10/site-packages/torchvision/image.so: undefined symbol: _ZN3c1017RegisterOperatorsD1Ev'If you don't plan on using image functionality from `torchvision.io`, you can ignore this warning. Otherwise, there might be something wrong with your environment. Did you have `libjpeg` or `libpng`

In [9]:
tokenizer_path: Path = Path("weights/tokenizer.model")
tokenizer = Tokenizer(tokenizer_path)
train_set =test_data
print(f"train has {len(train_set):,} samples")
print("Processing train split ...")

train has 11,320 samples
Processing train split ...


In [10]:
model.device

device(type='cuda', index=0)

In [11]:
result = []

def tokenize(tokenizer: Tokenizer, string: str, max_length: int, eos=True) -> torch.Tensor:
    return tokenizer.encode(string, bos=True, eos=eos, max_length=max_length)

instruction = 'You are an ASR transcript selector. You have a few transcripts generated by an automatic speech recognition model. Your task is to generate the most likely transcript from them. If the generated transcripts have grammatical or logical errors, you will modify them accordingly to produce the most accurate and coherent transcript.'

for i in tqdm(range(len(test_data))):        
    for name in test_data[i].keys():
        ip = test_data[i][name]
    inference = ip['inference']
    gt = ip['ground_truth']
        
    # Removing the ground_truth, if present among the inferences for the prompt
    if gt in inference:
        inference.remove(gt)
            
        # joining the inputs with '\n'
    for_input = '\n'.join(inference[:15])
    # The prompt follows the Aplaca template ; https://github.com/tatsu-lab/stanford_alpaca
    full_prompt = f"""Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.\n\n ### Instruction:\n{instruction}\n\n### Input:\n{for_input}\n\n### Response:"""
    full_prompt_and_response = full_prompt + gt

    encoded_full_prompt = tokenize(tokenizer, full_prompt, max_length=2048, eos=False)
    encoded_full_prompt_and_response = tokenize(tokenizer, full_prompt_and_response, eos=True, max_length=2048)
    labels = encoded_full_prompt_and_response.clone()
    labels_with_masked_input = encoded_full_prompt_and_response.clone()
    labels_with_masked_input[:len(encoded_full_prompt)] = -1
    
    path =  ip['path']
    audio = whisper.load_audio(path)  
    audio = whisper.pad_or_trim(audio)            
    mel = whisper.log_mel_spectrogram(audio).to(model.device)  # of shape (#channels =  80 ; #samples = )   
    mel = mel.unsqueeze(0)
    
    with torch.no_grad():
        audio_features  = model.encoder(mel)
        

    result.append( {**ip,'index':name, "input_ids": encoded_full_prompt_and_response, "input_ids_no_response": encoded_full_prompt, "labels": labels, 'labels_with_masked_input': labels_with_masked_input,'audio_features': audio_features.bfloat16()})

 50%|█████     | 5701/11320 [05:20<05:15, 17.80it/s]


OutOfMemoryError: CUDA out of memory. Tried to allocate 20.00 MiB. GPU 

: 

In [ ]:
result

In [ ]:
torch.save(result,'/ibex/user/radhaks/LLMs/LLaMA_7B/LLAMA_EMNLP_DeepSpeed/dataset/inferences/gigaspeech_train.pt')